In [10]:
import pandas as pd
import numpy as np
import sqlite3 
from matplotlib import pyplot as plt
from plotly import express as px

In [2]:
temps = pd.read_csv("temps.csv")

In [3]:
countries = pd.read_csv("countries.csv")

In [4]:
stations = pd.read_csv("station-metadata.csv")

In [5]:
connection = sqlite3.connect("data.db")

In [12]:
def query_climate_database(country, year_begin, year_end, month):
    '''
    Function that queries database consisting of 3 tables with user-specified parameters 
    and outputs a pandas dataframe that includes various measurements like locations, average temperature, etc. 
    
    Parameters:
    
    country = user-selected country
    year_begin = beginning of period range
    year_end = end of period range
    month = user-selected month
    
    Outputs:
    
    returns a pandas dataframe with relevant measurements
    '''
    
    # opens connection to the database with our 3 tables
    connection = sqlite3.connect("data.db")
    
    # set SQL query string that we will execute later 
    query = \
    '''
    SELECT S.name, S.latitude, S.longitude, C.name, T.year, T.month, T.temp
    FROM temperatures T
    LEFT JOIN stations S ON T.id = S.id
    LEFT JOIN countries C ON S.'fips 10-4' = C.'fips 10-4'
    WHERE (C.name = ?) AND (T.year BETWEEN ? AND ?) AND (T.month = ?)
    '''
    
    # transform results of query into pandas dataframe
    dataframe = pd.read_sql_query(query, connection, params = (country, year_begin, year_end, month)) 
    
    # close connection
    connection.close() 

    return dataframe


In [7]:
from sklearn.linear_model import LinearRegression

# calculate yearly change in temp

def avg_change_coef(data_frame):
    x = data_frame[["Year"]] 
    y = data_frame["Temp"]   
    LR = LinearRegression()
    LR.fit(x, y)
    return round(LR.coef_[0], 4)

In [8]:
def temperature_coefficient_plot(country, year_begin, year_end, month, min_obs, **kwargs):
    
    df = query_climate_database(country, year_begin, year_end, month)
    
    # count number of observations per station 
    df["Observations"] = df.groupby("NAME")["Temp"].transform(len)
    
    # calculate yearly change in temp
    avg_coefs = df.groupby(["NAME", "Month", "LATITUDE", "LONGITUDE", "Observations"]).apply(avg_change_coef)
    avg_coefs = avg_coefs.reset_index()
    avg_coefs = avg_coefs.rename(columns = {0 : "Estimated Yearly Change (C)"})
    
    # filter out stations that don't have min. number of years of data
    final_df = avg_coefs[avg_coefs["Observations"] >= min_obs]
    
    # create plot using updated df
    figure = px.scatter_mapbox(final_df,
                      lat = "LATITUDE",
                      lon = "LONGITUDE",
                      hover_name = "NAME", 
                               hover_data = ["Estimated Yearly Change (C)"], # insert calculated coefficients
                               color = "Estimated Yearly Change (C)", # set color based on coefs
                               color_continuous_midpoint = 0, 
                               title = "Estimated Average Yearly Temperature Change for Stations in India during January, 1980 - 2020",
                               **kwargs)
    
    return figure


In [13]:
color_map = px.colors.diverging.RdGy_r

fig = temperature_coefficient_plot("India", 1980, 2020, 1, 
          min_obs = 10,
         zoom = 2,
         mapbox_style = "carto-positron",
         color_continuous_scale = color_map)

fig.show()

In [14]:
from plotly.io import write_html
write_html(fig, "geographic_scatter.html")

In [15]:
def query_function_two(country_one, country_two, year_begin, year_end):
    '''
    Function that queries database and outputs a pandas dataframe that includes 
    various measurements like locations, average temperature, etc. 
    
    Parameters:
    
    country_one = user-selected first country 
    country_two user-selected second country
    year_begin = beginning of period range
    year_end = end of period range
    
    Outputs:
    
    Returns a pandas dataframe with relevant measurements
    '''
    
    # opens connection to the database with our 3 tables
    connection = sqlite3.connect("data.db")
    
    # set SQL query string that we will execute later 
    query = \
    '''
    SELECT S.name, C.name, T.month, T.year, T.temp
    FROM temperatures T
    LEFT JOIN stations S ON T.id = S.id
    LEFT JOIN countries C ON S.'fips 10-4' = C.'fips 10-4'
    WHERE ((C.name = ?) OR (C.name = ?)) AND (T.year BETWEEN ? AND ?)
    '''
    
    # transform results of query into pandas dataframe
    dataframe = pd.read_sql_query(query, connection, params = (country_one, country_two, year_begin, year_end)) 
    
    # close connection
    connection.close() 

    return dataframe

In [16]:
def scatter_plot_figure(country_one, country_two, year_begin, year_end, **kwargs):
    '''
    Function that uses query_function_two to filter out relevant data and creates a scatter plot figure using data
    
    Parameters:
    
    Same as query_function_two
    **kwargs = additional keyword arguments
    
    Output:
    Returns a scatter plot figure 
    '''
    
    # use second query function to filter data
    df = query_function_two(country_one, country_two, year_begin, year_end)
    
    # calculate mean temperature per year 
    df["Mean Temperature of Year (C)"] = df.groupby(["Name", "Year"])["Temp"].transform(np.mean)
    df["Mean Temperature of Year (C)"] = df["Mean Temperature of Year (C)"].round(3)

    # create scatter plot
    figure = px.scatter(df,
                    x = "Year",
                    y = "Mean Temperature of Year (C)",
                    hover_name = "NAME",
                        color = "Name",
                        facet_col = "Name",
                       opacity = 0.6,
                       height = 500,
                       width = 700,
                       **kwargs)
    
    return figure

In [18]:
fig = scatter_plot_figure("Antarctica", "Brazil", 1970, 2020,
                         title = "Average Yearly Temperature of Antarctica and Brazil from 1970 to 2020")


fig.show()

In [19]:

write_html(fig, "scatter.html")